In [1]:
import firedecomp.plot.simulations as plot_sim

import plotly
import plotly.graph_objs as go
import plotly.offline
plotly.offline.init_notebook_mode()
import qgrid

# Small Cases

In [2]:
df = plot_sim.read_csvs(folder="Small_cases", file="solution.csv")

File b'Small_cases\\execute.sh\\solution.csv' does not exist
File b'Small_cases\\m-AL_nb-2_na-4_nm-2_np-10\\solution.csv' does not exist
File b'Small_cases\\solver_options.yaml\\solution.csv' does not exist


We need also ``benders_scip`` (``20191225_small_benders/*``) method and ``m-AL_nb-2_na-4_nm-2_np-10`` (in execution in CESGA in ``20191213_small_AL/m-AL_nb-2_na-4_nm-2_np-10``).

In [3]:
qgrid.show_grid(df)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defaultColumnWidth': 150, 'rowHeight': 28, 'enableColumnReorder': False, 'enableTextSelectionOnCells': True, 'editable': True, 'autoEdit': False, 'explicitInitialization': True, 'maxVisibleRows': 15, 'minVisibleRows': 8, 'sortable': True, 'filterable': True, 'highlightSelectedCell': False, 'highlightSelectedRow': True, 'boldIndex': True}, id='199d28d4-a8b4-47a7-b38c-81c5d583bba1', precision=5)

Number of infeasible solutions per method:

In [4]:
for m in set(df['mode']):
    total = sum(df['mode'] == m)
    feasible = sum(df[df['mode'] == m]['constrvio'] < 0.0001)
    print(f"Mode {m}:")
    print(f"- Total: {total}")
    print(f"- Infeasible: {total - feasible}")
    print(f"- Percentaje: {(total - feasible)/total}")

Mode original:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875
Mode fix_work:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875
Mode AL:
- Total: 1500
- Infeasible: 35
- Percentaje: 0.023333333333333334
Mode gcg_scip:
- Total: 1600
- Infeasible: 165
- Percentaje: 0.103125


## Group by instances

In [5]:
groupby = ['num_brigades', 'num_aircraft', 'num_machines',
                   'num_periods', 'seed']

sense_instances = df.groupby(groupby)
obj_fun = sense_instances['obj_fun'].min()
df = df.set_index(groupby).reset_index()

In [6]:
grid_options = plot_sim.get_qgrid_options()

In [7]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defaultColumnWidth': 100, 'rowHeight': 28, 'enableColumnReorder': True, 'enableTextSelectionOnCells': True, 'editable': True, 'autoEdit': False, 'explicitInitialization': True, 'maxVisibleRows': 10, 'minVisibleRows': 10, 'sortable': True, 'filterable': True, 'highlightSelectedCell': False, 'highlightSelectedRow': True, 'boldIndex': True}, id='8384eeb5-6235-4239-80a6-f361f27a749d', precision=5)

## >>> Relative Elapsed Time (considering only feasible cases)

In [9]:
plot_sim.performance_profile_graph(df, x='rel_elapsed_time', filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: original
Scatter: fix_work
Scatter: AL
Scatter: gcg_scip


### Relative Elapsed Time taking into account only that cases that reach an optimal value (considering only feasible cases)

In [10]:
plot_sim.performance_profile_graph(df, x='rel_elapsed_time', conditions=[{'column': 'rel_obj_fun', 'operator': 'gt', 'value': 0.9999}], filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: original
Scatter: fix_work
Scatter: AL
Scatter: gcg_scip


### Solve Time taking into account only that cases that reach an optimal value (considering only feasible cases)

Interesting plot to check methods behaviour, but not for paper.

In [13]:
plot_sim.performance_profile_graph(df, x='solve_time', conditions=[{'column': 'rel_obj_fun', 'operator': 'gt', 'value': 0.9999}], filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: original
Scatter: fix_work
Scatter: AL
Scatter: gcg_scip


## >>> Relative objective function (only feasible cases)

In [17]:
plot_sim.performance_profile_graph(df, x='rel_obj_fun', filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: original
Scatter: fix_work
Scatter: AL
Scatter: gcg_scip


## Boxplots

**NOTA:** Únicamente los añadiría para el análisis de los resultados grandes.

Mirar por tamaño y tipo de instancias. Sacar funciones de densidad agregada (aporta más que el performance profile?) y por grupos.

In [21]:
plot_sim.sim_boxplot(df, y='solve_time', modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

In [25]:
plot_sim.sim_boxplot(plot_sim.get_best(df), y="rel_solve_time", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

Parece que ganamos en casi todos los casos menos en:
- 20-20- 5-20
-  5-20-20-20
-  5-20- 5-20

Todos estos casos se corresponden a los que tienen 20 periodos y el número máximo de aeronaves (20). Analizar que significan las diferencias que se observan entre *solve_time* y *rel_solve_time*.

In [26]:
plot_sim.sim_boxplot(df, y="obj_fun", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

In [27]:
plot_sim.sim_boxplot(plot_sim.get_best(df), y="rel_obj_fun", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

# Huge Cases

In [41]:
df = plot_sim.read_csvs(folder="Huge_cases", file="solution.csv")

In [42]:
grid_options = plot_sim.get_qgrid_options()

In [43]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defaultColumnWidth': 100, 'rowHeight': 28, 'enableColumnReorder': True, 'enableTextSelectionOnCells': True, 'editable': True, 'autoEdit': False, 'explicitInitialization': True, 'maxVisibleRows': 10, 'minVisibleRows': 10, 'sortable': True, 'filterable': True, 'highlightSelectedCell': False, 'highlightSelectedRow': True, 'boldIndex': True}, id='d70dfe73-989b-4757-bf6a-fa6d54e3ef91', precision=5)

Number of infeasible solutions per method:

In [44]:
for m in set(df['mode']):
    total = sum(df['mode'] == m)
    feasible = sum(df[df['mode'] == m]['constrvio'] < 0.0001)
    print(f"Mode {m}:")
    print(f"- Total: {total}")
    print(f"- Infeasible: {total - feasible}")
    print(f"- Percentaje: {(total - feasible)/total}")

Mode fix_work:
- Total: 4800
- Infeasible: 2
- Percentaje: 0.0004166666666666667
Mode original:
- Total: 4800
- Infeasible: 128
- Percentaje: 0.02666666666666667


## Group by instances

In [45]:
groupby = ['num_brigades', 'num_aircraft', 'num_machines',
                   'num_periods', 'seed']

sense_instances = df.groupby(groupby)
obj_fun = sense_instances['obj_fun'].min()
df = df.set_index(groupby).reset_index()

In [46]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defaultColumnWidth': 100, 'rowHeight': 28, 'enableColumnReorder': True, 'enableTextSelectionOnCells': True, 'editable': True, 'autoEdit': False, 'explicitInitialization': True, 'maxVisibleRows': 10, 'minVisibleRows': 10, 'sortable': True, 'filterable': True, 'highlightSelectedCell': False, 'highlightSelectedRow': True, 'boldIndex': True}, id='c16760ba-a46f-40a1-be0a-60d689996ed2', precision=5)

## >>> Relative Elapsed Time (considering only feasible cases)

In [34]:
plot_sim.performance_profile_graph(df, x='rel_elapsed_time', filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: fix_work
Scatter: original


### Relative Elapsed Time taking into account only that cases that reach an optimal value (considering only feasible cases)

In [35]:
plot_sim.performance_profile_graph(df, x='rel_elapsed_time', conditions=[{'column': 'rel_obj_fun', 'operator': 'gt', 'value': 0.9999}], filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: fix_work
Scatter: original


### Solve Time taking into account only that cases that reach an optimal value (considering only feasible cases)

Interesting plot to check methods behaviour, but not for paper.

In [36]:
plot_sim.performance_profile_graph(df, x='solve_time', conditions=[{'column': 'rel_obj_fun', 'operator': 'gt', 'value': 0.9999}], filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: fix_work
Scatter: original


## >>> Relative objective function (only feasible cases)

In [37]:
plot_sim.performance_profile_graph(df, x='rel_obj_fun', filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}])

Scatter: fix_work
Scatter: original


## Boxplots

Mirar por tamaño y tipo de instancias. Sacar funciones de densidad agregada (aporta más que el performance profile?) y por grupos.

In [38]:
plot_sim.sim_boxplot(df, y='solve_time', modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

In [39]:
plot_sim.sim_boxplot(plot_sim.get_best(df), y="rel_solve_time", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

Parece que ganamos en casi todos los casos menos en:
- 20-20- 5-20
-  5-20-20-20
-  5-20- 5-20

Todos estos casos se corresponden a los que tienen 20 periodos y el número máximo de aeronaves (20). Analizar que significan las diferencias que se observan entre *solve_time* y *rel_solve_time*.

In [40]:
plot_sim.sim_boxplot(df, y="obj_fun", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])

In [47]:
plot_sim.sim_boxplot(plot_sim.get_best(df), y="rel_obj_fun", modes=['AL', 'fix_work', 'original', 'gcg_scip'], columns=['num_brigades', 'num_aircraft', 'num_machines', 'num_periods'])